In [1]:
import numpy as np
import random

import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim

from matplotlib import pyplot as plt

from numpy import exp,arange
from pylab import meshgrid,cm,imshow,contour,clabel,colorbar,axis,title,show

In [2]:
# ==========
# helping methods
# ==========

# generate a list from lower and upper bound
def gen_list(p0, pn, delta, dig=5):
    ret = []
    i = p0
    while i < pn:
        ret.append(float(i))
        i += delta
        i = round(i, dig)
    return ret

# padding and zero padding
def padding(origin, a_list, b_list):
    return np.hstack((a_list, origin, b_list))

def zero_padding(origin, num):
    zero_list = [0 for i in range(num)]
    return padding(origin, zero_list, zero_list)

# trainning pairs
def gen_pair(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-1-length)
        train = current_t[p-length:p+length+1]
        solu = next_t[p]
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

# trainning pairs (in average)
def gen_pair_ave(u, x, t, length=3, num=1000):
    pairs = []
    for i in range(num):
        r = random.randint(0, t-2)
        current_t = u[r]
        next_t = u[r+1]
        p = random.randint(length, x-2-length)
        train0 = current_t[p-length:p+length+2]
        solu1 = next_t[p]
        solu2 = next_t[p+1]
        train = []
        for j in range(len(train0)-1):
                train.append(0.5 * (train0[j] + train0[j+1]))
        solu = 0.5 * (solu1 + solu2)
        pair = {'input': train, 'solu': solu}
        pairs.append(pair)
    return pairs

In [3]:
# the analytical representation of exact solution
def heat_equ_analytical_solu(x, t):
    return np.sin(np.pi * x) * np.exp(-np.power(np.pi, 2) * t)

In [4]:
# restnet
class ResNet(nn.Module):
    def __init__(self, i, h, o):
        super(ResNet, self).__init__()
        self.linear1 = nn.Linear(i, h)
        self.relu1 = nn.ReLU()
        self.linear2 = nn.Linear(h, o)
        self.relu2 = nn.ReLU()
        
    def forward(self, x):
        out = self.linear1(x)
        out = self.relu1(out)
        out = self.linear2(out)
        out = self.relu2(out)
        return out + torch.mean(x)

    def load_model(self, save_path):
        self.load_state_dict(torch.load(save_path))

    def save_model(self, save_path):
        torch.save(self.state_dict(), save_path)

## $\Delta x=\frac{1}{20}$ $\Delta t=\frac{1}{40}$

In [5]:
x_1 = arange(0, 2 * np.pi, 1/20)
t_1 = arange(0, 2 * np.pi, 1/40)
X_1,T_1 = meshgrid(x_1, t_1) # grid of point
Z_1 = heat_equ_analytical_solu(X_1, T_1) # evaluation of the function on the grid

In [6]:
# preparing the trainning set
data_pairs_1 = gen_pair_ave(Z_1, len(Z_1[0]), len(Z_1), length=3, num=10000)
print(data_pairs_1)

[{'input': [-5.174260200224773e-10, -4.614535519562689e-10, -3.941185659643618e-10, -3.170790728738825e-10, -2.3223204068413774e-10, -1.4166668491879426e-10, -4.7613025205978764e-11], 'solu': -2.4774774567780377e-10}, {'input': [1.1696511579776237e-05, 1.1696511579776235e-05, 1.140850464618577e-05, 1.083958246555005e-05, 1.0003753790100789e-05, 8.921599495783888e-06, 7.6197658127896214e-06], 'solu': 8.46943980120955e-06}, {'input': [-7.582982766709553e-21, -8.878532082240741e-21, -9.955462471748549e-21, -1.0787256334916244e-20, -1.1353432146267077e-20, -1.16400487782958e-20, -1.1640048778295798e-20], 'solu': -8.428555107095018e-21}, {'input': [6.9506260233279366e-15, 5.936395438404128e-15, 4.7759910960199004e-15, 3.4979860022459744e-15, 2.1338488839467918e-15, 7.171693242864207e-16, -7.171693242864257e-16], 'solu': 2.7331294323976137e-15}, {'input': [0.505877886047332, 0.5923069033844472, 0.6641513590063265, 0.7196422039774815, 0.7574130695311656, 0.7765339116031319, 0.776533911603132]

In [7]:
model_1 = ResNet(7, 6, 1)
optimizer_1 = optim.Adam(model_1.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_1 = nn.MSELoss()
model_1.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [8]:
list_of_loss_1 = []
list_of_output_1 = []
for data in data_pairs_1:
    output = model_1(torch.FloatTensor(data["input"]))
    loss = criterion_1(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_1.append(np.log10(loss.item()))
    list_of_output_1.append(output)
    model_1.zero_grad()
    loss.backward()
    optimizer_1.step()

<ipython-input-8-ac38450c9edb>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_1.append(np.log10(loss.item()))


In [9]:
list_of_loss_1_file = open('list_of_loss_12 xx.txt', 'w+')
for value in list_of_loss_1:
    list_of_loss_1_file.write(str(value)+" ")
list_of_loss_1_file.close()

list_of_output_1_file = open('list_of_output_12 xx.txt', 'w+')
for value in list_of_output_1:
    list_of_output_1_file.write(str(value)+" ")
list_of_output_1_file.close()

In [10]:
model_1.save_model("model_xx delta x=1 20 delta t=1 40")

## $\Delta x=\frac{1}{40}$ $\Delta t=\frac{1}{40}$

In [11]:
x_2 = arange(0, 2 * np.pi, 1/40)
t_2 = arange(0, 2 * np.pi, 1/40)
X_2,T_2 = meshgrid(x_2, t_2) # grid of point
Z_2 = heat_equ_analytical_solu(X_2, T_2) # evaluation of the function on the grid

In [12]:
# preparing the trainning set
data_pairs_2 = gen_pair_ave(Z_2, len(Z_2[0]), len(Z_2), length=3, num=10000)
print(data_pairs_2)

[{'input': [5.367699259197689e-24, 5.232377307616574e-24, 5.064796009991987e-24, 4.86598856075022e-24, 4.637180673926031e-24, 4.379783026228038e-24, 4.095382559747701e-24], 'solu': 3.802009654857798e-24}, {'input': [-4.418474142090429e-14, -6.147678657002111e-14, -7.838980688682775e-14, -9.481952797692132e-14, -1.1066465514634448e-13, -1.2582749791705817e-13, -1.4021457232122419e-13], 'solu': -7.408664371823556e-14}, {'input': [3.0622110796758344e-05, 9.1677536894329e-05, 0.00015216774049107152, 0.00021171977936677812, 0.00026996649539871625, 0.00032654877821355313, 0.00038111777922221696], 'solu': 0.00016542592224112027}, {'input': [1.19139312898352e-08, 1.069147193289833e-08, 9.403096096219947e-09, 8.056747045261623e-09, 6.660725469629006e-09, 5.223638306560143e-09, 3.754345676295332e-09], 'solu': 6.295088792421803e-09}, {'input': [-1.1984134929939164e-09, -1.107802037998475e-09, -1.010360615057214e-09, -9.06689982945128e-10, -7.974293055831695e-10, -6.832522113801393e-10, -5.6486264

In [13]:
model_2 = ResNet(7, 6, 1)
optimizer_2 = optim.Adam(model_2.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_2 = nn.MSELoss()
model_2.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [14]:
list_of_loss_2 = []
list_of_output_2 = []
for data in data_pairs_2:
    output = model_2(torch.FloatTensor(data["input"]))
    loss = criterion_2(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_2.append(np.log10(loss.item()))
    list_of_output_2.append(output)
    model_2.zero_grad()
    loss.backward()
    optimizer_2.step()

<ipython-input-14-de329c128c88>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_2.append(np.log10(loss.item()))


In [15]:
list_of_loss_2_file = open('list_of_loss_22 xx.txt', 'w+')
for value in list_of_loss_2:
    list_of_loss_2_file.write(str(value)+" ")
list_of_loss_2_file.close()

list_of_output_2_file = open('list_of_output_22 xx.txt', 'w+')
for value in list_of_output_2:
    list_of_output_2_file.write(str(value)+" ")
list_of_output_2_file.close()

In [16]:
model_2.save_model("model_xx delta x=1 40 delta t=1 40")

## $\Delta x=\frac{1}{80}$ $\Delta t=\frac{1}{40}$

In [17]:
x_3 = arange(0, 2 * np.pi, 1/80)
t_3 = arange(0, 2 * np.pi, 1/40)
X_3,T_3 = meshgrid(x_3, t_3) # grid of point
Z_3 = heat_equ_analytical_solu(X_3, T_3) # evaluation of the function on the grid

In [18]:
# preparing the trainning set
data_pairs_3 = gen_pair_ave(Z_3, len(Z_3[0]), len(Z_3), length=3, num=10000)
print(data_pairs_3)

[{'input': [1.799947693216609e-14, 1.697168964981406e-14, 1.591773325215462e-14, 1.4839232863560677e-14, 1.3737851453460181e-14, 1.2615287272157792e-14, 1.1473271232255991e-14], 'solu': 1.1594541564076749e-14}, {'input': [1.356045042659658e-14, 1.8955348635588772e-14, 2.432101907089584e-14, 2.964918825761821e-14, 3.493164054506337e-14, 4.016023077468386e-14, 4.532689683932149e-14], 'solu': 2.3166207360910836e-14}, {'input': [6.988075210507745e-19, 6.849618092358251e-19, 6.700599359580564e-19, 6.541248788259537e-19, 6.371812085426183e-19, 6.192550510195247e-19, 6.003740470922609e-19], 'solu': 5.110963730657662e-19}, {'input': [-2.160187462033671e-25, -2.1327956398344317e-25, -2.1021152013466783e-25, -2.0681934535827983e-25, -2.0310827014191452e-25, -1.9908401669457144e-25, -1.9475279012338272e-25], 'solu': -1.6159699885161766e-25}, {'input': [6.203628613608078e-20, 7.308899080903064e-20, 8.40289975557487e-20, 9.483943767877953e-20, 1.0550364226300827e-19, 1.1600516787792398e-19, 1.26327

In [19]:
model_3 = ResNet(7, 6, 1)
optimizer_3 = optim.Adam(model_3.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_3 = nn.MSELoss()
model_3.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [20]:
list_of_loss_3 = []
list_of_output_3 = []
for data in data_pairs_3:
    output = model_3(torch.FloatTensor(data["input"]))
    loss = criterion_3(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_3.append(np.log10(loss.item()))
    list_of_output_3.append(output)
    model_3.zero_grad()
    loss.backward()
    optimizer_3.step()

<ipython-input-20-3f959fb14d49>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_3.append(np.log10(loss.item()))


In [21]:
list_of_loss_3_file = open('list_of_loss_32 xx.txt', 'w+')
for value in list_of_loss_3:
    list_of_loss_3_file.write(str(value)+" ")
list_of_loss_3_file.close()

list_of_output_3_file = open('list_of_output_32 xx.txt', 'w+')
for value in list_of_output_3:
    list_of_output_3_file.write(str(value)+" ")
list_of_output_3_file.close()

In [22]:
model_3.save_model("model_xx delta x=1 80 delta t=1 40")

## $\Delta x=\frac{1}{160}$ $\Delta t=\frac{1}{40}$

In [23]:
x_4 = arange(0, 2 * np.pi, 1/160)
t_4 = arange(0, 2 * np.pi, 1/40)
X_4,T_4 = meshgrid(x_4, t_4) # grid of point
Z_4 = heat_equ_analytical_solu(X_4, T_4) # evaluation of the function on the grid

In [24]:
# preparing the trainning set
data_pairs_4 = gen_pair_ave(Z_4, len(Z_4[0]), len(Z_4), length=3, num=10000)
print(data_pairs_4)

[{'input': [-1.5039252422705596e-17, -1.430321808707449e-17, -1.3561669588596616e-17, -1.281489280833412e-17, -1.2063175642951444e-17, -1.1306807893725363e-17, -1.0546081154821254e-17], 'solu': -1.0012836153429411e-17}, {'input': [1.4780754188897606e-20, 1.482679349816824e-20, 1.4867116796304414e-20, 1.490170853790711e-20, 1.493055538720145e-20, 1.4953646223177905e-20, 1.4970972143879656e-20], 'solu': 1.1643356540539058e-20}, {'input': [-4.136890219310863e-21, -5.789413344930795e-21, -7.439704541499659e-21, -9.087127590346598e-21, -1.0731047378526076e-20, -1.2370830143666307e-20, -1.4005843718296712e-20], 'solu': -7.100170171402028e-21}, {'input': [0.00034751763643704736, 0.0003611730446946719, 0.00037468921386832376, 0.00038806093321749413, 0.0004012830476898315, 0.00041435045990851217, 0.0004272581321373765], 'solu': 0.0003032089772398796}, {'input': [3.317819775866803e-19, 3.349569692044692e-19, 3.3800282853443214e-19, 3.4091838133981706e-19, 3.4370250361951756e-19, 3.46354122041396

In [25]:
model_4 = ResNet(7, 6, 1)
optimizer_4 = optim.Adam(model_4.parameters(), lr=0.001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0, amsgrad=False)
criterion_4 = nn.MSELoss()
model_4.train()

ResNet(
  (linear1): Linear(in_features=7, out_features=6, bias=True)
  (relu1): ReLU()
  (linear2): Linear(in_features=6, out_features=1, bias=True)
  (relu2): ReLU()
)

In [26]:
list_of_loss_4 = []
list_of_output_4 = []
for data in data_pairs_4:
    output = model_4(torch.FloatTensor(data["input"]))
    loss = criterion_4(output, torch.FloatTensor([data["solu"]]))
    list_of_loss_4.append(np.log10(loss.item()))
    list_of_output_4.append(output)
    model_4.zero_grad()
    loss.backward()
    optimizer_4.step()

<ipython-input-26-f52da78e2a74>:6: RuntimeWarning: divide by zero encountered in log10
  list_of_loss_4.append(np.log10(loss.item()))


In [27]:
list_of_loss_4_file = open('list_of_loss_42 xx.txt', 'w+')
for value in list_of_loss_4:
    list_of_loss_4_file.write(str(value)+" ")
list_of_loss_4_file.close()

list_of_output_4_file = open('list_of_output_42 xx.txt', 'w+')
for value in list_of_output_4:
    list_of_output_4_file.write(str(value)+" ")
list_of_output_4_file.close()

In [28]:
model_4.save_model("model_xx delta x=1 160 delta t=1 40")